In [1]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
H =0.25
shape = Rectangle(1,H).Face()
shape.edges.Min(X).name="inlet"
shape.edges.Max(X).name="outlet"
shape.edges.Min(Y).name="wall"
shape.edges.Max(Y).name="wall"
mesh = Mesh(OCCGeometry(shape, dim=2).GenerateMesh(maxh=0.05))


T = Parameter(0.00)
nu = CF(1)
k = 2
V = VectorH1(mesh,order=k, dirichlet="wall|inlet|outlet")
Q = H1(mesh,order=k-1)
# X = V*Q
R = NumberSpace(mesh)

X = FESpace([V,Q,R]) 
(u,p,lam1),(v,q, mu1) = X.TnT()

gfu = GridFunction(X)
velocity, pressure, dump = gfu.components
# parabolic inflow at bc=1:

uin = CoefficientFunction((1.0*4*y*(H-y)*(sin(T)**2)/(H*H),0))
velocity.Set(uin,definedon=mesh.Boundaries("inlet|wall|outlet"))

# (u,p), (v,q) = X.TnT()

a = BilinearForm(X)
stokes = (2*nu*InnerProduct(Sym(grad(u)),Sym(grad(v)))-div(u)*q-div(v)*p)*dx + p*mu1*dx + q*lam1*dx
a += stokes
a.Assemble()

f = LinearForm(X)
f.Assemble()

mass = BilinearForm(X)
mass += InnerProduct(u,v)*dx
mass.Assemble()


res = f.vec - a.mat*gfu.vec
inv_stokes = a.mat.Inverse(X.FreeDofs())
gfu.vec.data += 0*inv_stokes * res
dt = 0.01

# matrix for implicit part of IMEX(1) scheme:
mstar = BilinearForm(X)
mstar += (1/dt)*InnerProduct(u,v)*dx + InnerProduct(2*nu*Sym(grad(u)),Sym(grad(v)))*dx - div(u)*q*dx - div(v)*p*dx + p*mu1*dx + q*lam1*dx
mstar.Assemble()
inv = mstar.mat.Inverse(X.FreeDofs())

tend = 5
gfut = GridFunction(gfu.space,multidim=0)

gfut.AddMultiDimComponent(gfu.vec)
t = 0; cnt = 0
while t < tend-0.5*dt:
    print ("\rt=", t, end="")
    if t < pi/2: # Stop updating time here, as sin(pi/2)^2 = 1
        T.Set(t)
        velocity.Set(uin,definedon=mesh.Boundaries("inlet|wall|outlet"))

    velocity.Set(uin,definedon=mesh.Boundaries("inlet|wall|outlet"))

    res = -a.mat* gfu.vec + f.vec
    gfu.vec.data += inv * res

    t = t + dt; cnt += 1

    if cnt % 10 == 0:
        gfut.AddMultiDimComponent(gfu.vec)

gfut.AddMultiDimComponent(gfu.vec)

t= 4.989999999999938575

In [2]:
Draw(gfut.components[0],mesh, animate = True, min = 0, max = 1.1)
Draw(gfut.components[1],mesh, animate = True, min = -64, max = 64)

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

BaseWebGuiScene